In [2]:
%load_ext autoreload
%autoreload 2

In [3]:
from requests import ReadTimeout, HTTPError, exceptions
from http import client

SSLError = exceptions.SSLError
RemoteDisconnected = client.RemoteDisconnected

import json
import time
from steam.webapi import WebAPI
from SteamUser import *
import concurrent.futures

with open("steam.key") as key:
    API = WebAPI(key.read())

In [4]:
def create_user(id):
    u = SteamUser(id)
    errorAttempt = 0
    attemptTries = 3
    waitTime = 5
    #Summary Data
    while True:
        try:
            summary = API.ISteamUser.GetPlayerSummaries(steamids=id)['response']['players']
            if len(summary) == 0: summary = {}
            else: summary = summary[0]
            
            u.personaname = summary.get('personaname')
            u.profileurl = summary.get('profileurl')
            u.avatar = summary.get('avatar')
            u.avatarmedium = summary.get('avatarmedium')
            u.avatarfull = summary.get('avatarfull')
            u.personstate = summary.get('personstate')
            u.communityvisibilitystate = summary.get('communityvisibilitystate')
            u.profilestate = summary.get('profilestate')
            u.lastlogoff = summary.get('lastlogoff')
            u.commentpermission = summary.get('commentpermission')

            u.realname = summary.get('realname')
            u.primaryclanid = summary.get('primaryclanid')
            u.timecreated = summary.get('timecreated')
            u.gameid = summary.get('gameid')
            u.cityid = summary.get('cityid')
            u.loccountrycode = summary.get('loccountrycode')
            u.locstatecode = summary.get('locstatecode')
            u.loccityid = summary.get('loccityid')

        except ReadTimeout:
            if errorAttempt > attemptTries:
                print("Timed out retrys reached - cancelling id - {}".format(id))

                break

            print("Timed out - waiting {} seconds and trying again!".format(waitTime))
            time.sleep(waitTime)
            errorAttempt += 1

            continue

        except SSLError:
            if errorAttempt > attemptTries:
                print("SSLError retrys reached - cancelling id - {}".format(id))
                
                break

            print("Timed out SSLError - waiting {} seconds and trying again! - Summary".format(waitTime))
            time.sleep(waitTime)
            errorAttempt += 1

            continue

        except HTTPError:
            if errorAttempt > attemptTries:
                print("HTTPError retrys reached - cancelling id - {}".format(id))
                
                break

            print("Timed out HTTPError - waiting {} seconds and trying again!".format(waitTime))
            time.sleep(waitTime)
            errorAttempt += 1

            continue

        except:
            print("Unknown Error - {} user".format(id))
        break

    #Friends Data
    while True:
        try:
            friends = API.ISteamUser.GetFriendList(steamid=id)['friendslist']['friends']
            u.friends = list([f['steamid'] for f in friends])
        
        except ReadTimeout:
            if errorAttempt > attemptTries:
                print("Timed out retrys reached - cancelling id - {}".format(id))
                
                break

            print("Timed out - waiting {} seconds and trying again!".format(waitTime))
            time.sleep(waitTime)
            errorAttempt += 1

            continue

        except SSLError:
            if errorAttempt > attemptTries:
                print("SSLError retrys reached - cancelling id - {}".format(id))
                
                break

            print("Timed out SSLError - waiting {} seconds and trying again!".format(waitTime))
            time.sleep(waitTime)
            errorAttempt += 1

            continue

        except RemoteDisconnected:
            if errorAttempt > attemptTries:
                print("Timed out retrys reached - cancelling id - {}".format(id))
                
                break

            print("Timed out - waiting {} seconds and trying again!".format(waitTime))
            time.sleep(waitTime)
            errorAttempt += 1

            continue

        except HTTPError:
            break

        except:
            print("Unknown Error - {} user".format(id))
        
        break

    #Games Data
    while True:
        try:
            games = API.IPlayerService.GetOwnedGames_v1(
                steamid=int(id),
                include_appinfo=0,
                include_played_free_games=1,
                appids_filter=0,
                include_free_sub=0)['response']

            u.games = list([g['appid'] for g in games['games']])
            u.playtime = dict({a['appid']:a.get('playtime_forever') for a in games['games']})
            u.recent_playtime = dict({a['appid']:a.get('playtime_2weeks') for a in games['games']})
            u.total_playtime = sum(u.playtime.values())

        except ReadTimeout:
            if errorAttempt > attemptTries:
                print("Timed out retrys reached - cancelling id - {}".format(id))
                
                break

            print("Timed out - waiting {} seconds and trying again!".format(waitTime))
            time.sleep(waitTime)
            errorAttempt += 1

            continue

        except SSLError:
            if errorAttempt > attemptTries:
                print("SSLError retrys reached - cancelling id - {}".format(id))
                
                break

            print("Timed out SSLError - waiting {} seconds and trying again!".format(waitTime))
            time.sleep(waitTime)
            errorAttempt += 1

            continue

        except RemoteDisconnected:
            if errorAttempt > attemptTries:
                print("Timed out retrys reached - cancelling id - {}".format(id))
                
                break

            print("Timed out - waiting {} seconds and trying again!".format(waitTime))
            time.sleep(waitTime)
            errorAttempt += 1

            continue

        except HTTPError:
            if errorAttempt > attemptTries:
                print("HTTPError retrys reached - cancelling id - {}".format(id))
                
                break

            print("Timed out HTTPError - waiting {} seconds and trying again! - Games".format(waitTime))
            time.sleep(waitTime)
            errorAttempt += 1

            continue

        except KeyError:
            break

        except:
            print("Unknown Error - {} user".format(id))

        break
    
    #Groups Data
    while True:
        try:
            groups = API.ISteamUser.GetUserGroupList(steamid=id)['response']['groups']

            u.groups = list([g['gid'] for g in groups])

        except ReadTimeout:
            if errorAttempt > attemptTries:
                print("Timed out retrys reached - cancelling id - {}".format(id))
                
                continue

            print("Timed out - waiting {} seconds and trying again!".format(waitTime))
            time.sleep(waitTime)
            errorAttempt += 1

            continue

        except SSLError:
            if errorAttempt > attemptTries:
                print("SSLError retrys reached - cancelling id - {}".format(id))
                
                break

            print("Timed out SSLError - waiting {} seconds and trying again! - G".format(waitTime))
            time.sleep(waitTime)
            errorAttempt += 1

            continue

        except RemoteDisconnected:
            if errorAttempt > attemptTries:
                print("Timed out retrys reached - cancelling id - {}".format(id))
                
                break

            print("Timed out - waiting {} seconds and trying again!".format(waitTime))
            time.sleep(waitTime)
            errorAttempt += 1

            continue

        except HTTPError:
            break

        except:
            print("Unknown Error - {} user".format(id))

        break

    #Level and Badges Data
    while True:
        try:
            badges = API.IPlayerService.GetBadges(steamid=id)['response']
            u.playerxp = badges.get('playerxp')
            u.level = badges.get('player_level')
            u.badges = badges.get('badges')

        except ReadTimeout:
            if errorAttempt > attemptTries:
                print("Timed out retrys reached - cancelling id - {}".format(id))
                
                break

            print("Timed out - waiting {} seconds and trying again!".format(waitTime))
            time.sleep(waitTime)
            errorAttempt += 1

            continue

        except SSLError:
            if errorAttempt > attemptTries:
                print("SSLError retrys reached - cancelling id - {}".format(id))
                
                break

            print("Timed out SSLError - waiting {} seconds and trying again! - LB".format(waitTime))
            time.sleep(waitTime)
            errorAttempt += 1

            continue

        except RemoteDisconnected:
            if errorAttempt > attemptTries:
                print("Timed out retrys reached - cancelling id - {}".format(id))
                
                break

            print("Timed out - waiting {} seconds and trying again!".format(waitTime))
            time.sleep(waitTime)
            errorAttempt += 1

            continue

        except HTTPError:
            break

        except:
            print("Unknown Error - {} user".format(id))

        break

    #Bans Data
    while True:
        try:
            bans = API.ISteamUser.GetPlayerBans(steamids=id)['players']
            if len(bans) == 0: bans = {}
            else: bans = bans[0]
            
            u.communitybanned = bans.get('CommunityBanned')
            u.vacbanned = bans.get('VACBanned')
            u.numberofvacbans = bans.get('NumberOfVACBans')
            u.dayssincelastban = bans.get('DaysSinceLastBan')
            u.numberofgamebans = bans.get('NumberOfGameBans')
            u.economyban = bans.get('EconomyBan')
            
        except ReadTimeout:
            if errorAttempt > attemptTries:
                print("Timed out retrys reached - cancelling id - {}".format(id))
                
                break

            print("Timed out - waiting {} seconds and trying again!".format(waitTime))
            time.sleep(waitTime)
            errorAttempt += 1

            continue

        except SSLError:
            if errorAttempt > attemptTries:
                print("SSLError retrys reached - cancelling id - {}".format(id))
                
                break

            print("Timed out SSLError - waiting {} seconds and trying again!".format(waitTime))
            time.sleep(waitTime)
            errorAttempt += 1

            continue

        except RemoteDisconnected:
            if errorAttempt > attemptTries:
                print("Timed out retrys reached - cancelling id - {}".format(id))
                
                break

            print("Timed out - waiting {} seconds and trying again!".format(waitTime))
            time.sleep(waitTime)
            errorAttempt += 1

            continue

        except HTTPError:
            if errorAttempt > attemptTries:
                print("HTTPError retrys reached - cancelling id - {}".format(id))
                
                break

            print("Timed out HTTPError - waiting {} seconds and trying again! - Bans".format(waitTime))
            time.sleep(waitTime)
            errorAttempt += 1

            continue

        except:
            print("Unknown Error - {} user".format(id))
            
        break
    
    return u

In [5]:
usr = create_user('INSERT STEAM ID')

In [5]:
SD = 4
SI = 'INSERT STEAM ID'

users = {}

ids = set([SI])


def search(id):
    if not id in users:
        u = create_user(id)
        users[id] = u

        if not u.friends == None and not ((i + 1) == SD):
            return set(u.friends)

    return set()

for i in range(SD):
    print("Starting stage - {} - Collected {} users with {} more friends".format(i, len(users), len(ids)))
    exe = concurrent.futures.ThreadPoolExecutor(max_workers=512)
    f = list(exe.map(search, ids))

    ids = set.union(*(ff for ff in f))

Starting stage - 0 - Collected 0 users with 1 more friends
Starting stage - 1 - Collected 1 users with 9 more friends
Starting stage - 2 - Collected 10 users with 617 more friends
Unknown Error - 76561198091389181 userUnknown Error - 76561198089887050 user

Unknown Error - 76561198272231628 userUnknown Error - 76561198122218498 user

Unknown Error - 76561198279757398 user
Unknown Error - 76561198129399860 userUnknown Error - 76561198095342622 user

Unknown Error - 76561198098806933 userUnknown Error - 76561198142101852 user
Unknown Error - 76561198108932789 userUnknown Error - 76561198156619313 user


Unknown Error - 76561199078869629 user
Unknown Error - 76561198123817791 user
Unknown Error - 76561198059922812 user
Unknown Error - 76561198119124504 userUnknown Error - 76561198110612848 userUnknown Error - 76561198090284743 user
Unknown Error - 76561198135186462 userUnknown Error - 76561198057790635 userUnknown Error - 76561198103502250 user

Unknown Error - 76561198106761804 userUnkno

In [7]:
len(users)

35250

In [13]:
with open("INSERT FILE NAME", "w") as file:
    for v in users.values():
        file.write(json.dumps(v.asdict()) + "\n")
    file.close()